## Demo (Neuromeka TVE) - White board sweeping

### Prepare the task scene
* Prepare 2 Indy7, and install sweeping tool to indy. (Check release/Figs/7.1.WhiteBoardSweeping.jpg)
* Prepare "floor", "track", "box1", "box2" objects as defined in pkg.detector.aruco.marker_config.py
* The robots and "track" are installed on "floor".
* "box1" and "box2" are on "track"

## set running directory to project source

In [1]:
import os

os.chdir(os.path.join(os.environ["RNB_PLANNING_DIR"], 'src'))
from pkg.utils.code_scraps import add_indy_sweep_tool, add_indy_gripper_asm3, \
        use_current_place_point_only, use_current_sub_binders_only, \
        finish_L_shape, set_l_shape_object, ModeSwitcher, double_sweep_motions

## init combined robot config

In [2]:
from pkg.controller.combined_robot import *
from pkg.project_config import *
INDY_IP = "192.168.21.6"
INDY_IP2 = "192.168.21.2"

crob = CombinedRobot(robots_on_scene=[
    RobotConfig(0, RobotType.indy7, ((0.3,-0.4,0), (0,0,np.pi/2)),
                INDY_IP),
    RobotConfig(1, RobotType.indy7, ((-0.3,-0.4,0), (0,0,np.pi/2)),
                INDY_IP2, specs={"no_sdk": True})]
              , connection_list=[False, False])

crob.home_pose = np.multiply(
    [0,0,-0.5,0,-0.5,0,
     0,0,-0.5,0,-0.2,0],np.pi)
crob.home_dict = list2dict(crob.home_pose, crob.joint_names)
crob.reset_connection(True,True)

connection command:
indy0: False
indy1: False
connection command:
indy0: True
indy1: True
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.2)


In [3]:
indy0 = crob.robot_dict["indy0"]
indy1 = crob.robot_dict["indy1"]

indy1.grasp_ref = False
indy1.collision_policy = POLICY_NO_COLLISION_DETECTION

with indy0:
    if indy0.get_robot_status()["ready"] != 1:
        indy0.reset()
        
with indy1:
    if indy1.get_robot_status()["ready"] != 1:
        indy1.reset()

Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.2)


## Reset robots

In [7]:
time.sleep(3)

with indy0:
    while (indy0.get_robot_status()['resetting']):
        time.sleep(0.5)
    
with indy1:
    while (indy1.get_robot_status()['resetting']):
        time.sleep(0.5)
        
with indy1:
    indy1.stop_current_program()
time.sleep(0.5)
        
crob.joint_move_make_sure(crob.home_pose)

Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.2)
Connect: Server IP (192.168.21.2)
Header check fail (cmdId): Request 17, Response 9999
ErrorCode 19: No proper program state
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.2)


# Init camera

In [8]:
from pkg.detector.aruco.marker_config import *
from pkg.detector.aruco.stereo import ArucoStereo
from pkg.detector.camera.realsense import RealSense
from pkg.detector.camera.kinect import Kinect
aruco_map = get_aruco_map()
stereo = ArucoStereo(aruco_map, [Kinect(), RealSense()])
stereo.initialize()
_ = stereo.calibrate()

Device configuration: 
	color_format: 3 
	(0:JPG, 1:NV12, 2:YUY2, 3:BGRA32)

	color_resolution: 5 
	(0:OFF, 1:720p, 2:1080p, 3:1440p, 4:1536p, 5:2160p, 6:3072p)

	depth_mode: 3 
	(0:OFF, 1:NFOV_2X2BINNED, 2:NFOV_UNBINNED,3:WFOV_2X2BINNED, 4:WFOV_UNBINNED, 5:Passive IR)

	camera_fps: 2 
	(0:5 FPS, 1:15 FPS, 2:30 FPS)

	synchronized_images_only: False 
	(True of False). Drop images if the color and depth are not synchronized

	depth_delay_off_color_usec: 0 ms. 
	Delay between the color image and the depth image

	wired_sync_mode: 0
	(0:Standalone mode, 1:Master mode, 2:Subordinate mode)

	subordinate_delay_off_master_usec: 0 ms.
	The external synchronization timing.

	disable_streaming_indicator: False 
	(True or False). Streaming indicator automatically turns on when the color or depth camera's are in use.


Start streaming


## create scene builder

In [9]:
from pkg.geometry.builder.scene_builder import SceneBuilder
s_builder = SceneBuilder(stereo)
# deprecated: s_builder.reset_reference_coord(ref_name="floor")

## detect robot and make geometry scene
* **[IMPORTANT]** Make sure robot is visible, or correct saved file is used

In [10]:
# xyz_rpy_robots = s_builder.detect_items(level_mask=[DetectionLevel.ROBOT])
# save_pickle("data/xyz_rpy_robots.pkl", xyz_rpy_robots)
xyz_rpy_robots = load_pickle("data/xyz_rpy_robots.pkl")
crob.update_robot_pos_dict(xyz_rpy_robots=xyz_rpy_robots)
gscene = s_builder.create_gscene(crob)

Unable to register with master node [http://localhost:11311]: master may not be running yet. Will keep trying.
Please create a subscriber to the marker
publication OK
published: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]


## init planning pipeline

In [11]:
from pkg.planning.scene import PlanningScene
pscene = PlanningScene(gscene, combined_robot=crob)

from pkg.planning.pipeline import PlanningPipeline
ppline = PlanningPipeline(pscene)

from pkg.ui.ui_broker import *

# start UI
ui_broker = UIBroker.instance()
ui_broker.initialize(ppline, s_builder)
ui_broker.start_server()

ui_broker.set_tables()

Dash is running on http://0.0.0.0:8050/

 * Serving Flask app "pkg.ui.dash_launcher" (lazy loading)
 * Environment: production


```
open web ui on <your ip>:8050
click geometry items / Handles / Binders to highlight geometry on RVIZ
other functions may be buggy.. please report
```

## add environment
* **[IMPORTANT]** Make sure environment items are visible, or correct saved file is used

In [12]:
gtem_dict = s_builder.detect_and_register(level_mask=[DetectionLevel.ENVIRONMENT])

# add cam poles
ptems = s_builder.add_poles({"cam0": s_builder.ref_coord_inv[:3,3], "cam1":np.matmul(s_builder.ref_coord_inv, stereo.T_c12)[:3,3]},
                            color=(0.6,0.6,0.6,0.0))
gtems = s_builder.add_robot_geometries(color=(0,1,0,0.5), display=True, collision=True)
gscene.NAME_DICT["floor"].dims = (2,1,0.01)
gscene.set_workspace_boundary( -0.8, 0.8, -0.5, 0.5, -0.1, 0.9)

   Use a production WSGI server instead.
 * Debug mode: off
Please create a subscriber to the marker


In [13]:
gscene.update_markers_all()

## add environmental components

In [14]:
from pkg.planning.constraint.constraint_actor import Gripper2Tool, PlacePlane, SweepFramer, FixtureSlot
from pkg.planning.constraint.constraint_subject import \
        CustomObject, Grasp2Point, PlacePoint, SweepFrame, SweepTask, BoxObject, FixturePoint, AbstractObject

from pkg.planning.constraint.constraint_common import MotionConstraint
from pkg.planning.constraint.constraint_subject import AbstractTask
from pkg.planning.constraint.constraint_subject import SweepLineTask

add_indy_sweep_tool(gscene, "indy0", face_name="brush_face", tool_offset=0.108)
add_indy_gripper_asm3(gscene, "indy1")

gscene.create_safe(gtype=GEOTYPE.SPHERE, name="grip1", link_name="indy1_tcp", 
                 dims=(0.01,)*3, center=(0,0,0.12), rpy=(-np.pi/2,0,0), color=(1,0,0,1), display=True, collision=False, fixed=True)

pscene.create_binder(bname="grip1", gname="grip1", _type=Gripper2Tool, point=(0,0,0), rpy=(0,0,0))
pscene.create_binder(bname="brush_face", gname="brush_face", _type=SweepFramer, point=(0,0,gscene.NAME_DICT['brush_face'].dims[2]/2), 
                     rpy=(0,np.pi,0))

track = s_builder.detect_and_register(item_names=["track"], level_mask=[DetectionLevel.ENVIRONMENT])["track"]
track_face = gscene.copy_from(track, new_name="track_face", collision=False)
track_face.dims = (track.dims[0]-0.1, track.dims[1]-0.15, track.dims[2])
pscene.create_binder(bname="track_face", gname="track_face", _type=PlacePlane, point=None)
# track.dims = (track.dims[0]-0.32, track.dims[1]-0.12, track.dims[2])

gscene.update_markers_all()

TOOL_DIM = [0.06, 0.10]
TACK_WIDTH = 0.16
TRACK_DIM = track_face.dims
TRACK_NUM = np.ceil(np.divide(TRACK_DIM[1]-TOOL_DIM[1], TOOL_DIM[1])).astype(np.int)+1
TRACK_STEP = (TRACK_DIM[1]-TOOL_DIM[1])/(TRACK_NUM-1)
WP_REF_A = -np.subtract(TRACK_DIM[:2], TOOL_DIM[:2])/2
WP_REF_B = np.array([-WP_REF_A[0], WP_REF_A[1]])
WP_REF_M = np.array([0, WP_REF_A[1]])
TRC_THIC = TRACK_DIM[2]
FC_THIC = 2e-3
track_list = []
for i_trc in range(TRACK_NUM):
    wp1 = gscene.create_safe(GEOTYPE.BOX, "wp{}a".format(i_trc+1), "base_link", (TOOL_DIM[0]/2,TOOL_DIM[1]/2,TRC_THIC), 
                             tuple(WP_REF_A+[0,TRACK_STEP*i_trc])+(0,),rpy=(0,0,0), 
                             color=(0.8,0.2,0.2,0.2), display=True, fixed=True, collision=False, parent="track_face")
    wp2 = gscene.create_safe(GEOTYPE.BOX, "wp{}b".format(i_trc+1), "base_link", (TOOL_DIM[0]/2,TOOL_DIM[1]/2,TRC_THIC), 
                             tuple(WP_REF_B+[0,TRACK_STEP*i_trc])+(0,),rpy=(0,0,0), 
                             color=(0.8,0.2,0.2,0.2), display=True, fixed=True, collision=False, parent="track_face")
    face = gscene.create_safe(GEOTYPE.BOX, "face{}".format(i_trc+1), "base_link", 
                              (TRACK_DIM[0] - TOOL_DIM[0]/2,TACK_WIDTH,FC_THIC), 
                             center=tuple(WP_REF_M+[0,TRACK_STEP*i_trc])+(TRACK_DIM[2]/2 + FC_THIC/2,),rpy=(0,0,0), 
                             color=(0.8,0.2,0.2,0.2), display=True, fixed=True, collision=False, parent="track_face")
    track_list.append((wp1, wp2, face))
    
    gscene.update_markers_all()

sweep_list = []
for i_t, track_tem in enumerate(track_list):
    wp1, wp2, face = track_tem
    sweep_ = pscene.create_subject(oname="sweep{}".format(i_t+1), gname="track_face", _type=SweepLineTask, 
                                   action_points_dict = {wp1.name: SweepFrame(wp1.name, wp1, [0,0,0.005], [0,0,0]),
                                                       wp2.name: SweepFrame(wp2.name, wp2, [0,0,0.005], [0,0,0])}, 
                                   clearance=[face])
    sweep_list.append(sweep_)
    


## add movable objects

In [15]:
gtem_dict = s_builder.detect_and_register(level_mask=[DetectionLevel.MOVABLE])
gscene.update_markers_all()
    
for gname in sorted(gtem_dict.keys()):
    pscene.create_subject(oname=gname, gname=gname, _type=BoxObject, hexahedral=True)

# ## add blocking structure on table
# gscene.create_safe(gtype=GEOTYPE.BOX, name="blocker", link_name="base_link",
#                             center=(-0.27,-0.2,0.15), dims=(0.1,0.3, 0.4), rpy=(0,0,0), color=(0.0,0.8,0.0,0.5),
#                             collision=True, fixed=True)

### planners

In [16]:
from pkg.planning.motion.moveit.moveit_planner import MoveitPlanner
mplan = MoveitPlanner(pscene, enable_dual=False)
mplan.update_gscene()
from pkg.planning.task.rrt import TaskRRT
tplan = TaskRRT(pscene)
tplan.prepare()
ppline.set_motion_planner(mplan)
ppline.set_task_planner(tplan)

In [17]:
from pkg.planning.filtering.grasp_filter import GraspChecker
from pkg.planning.filtering.reach_filter import ReachChecker
from pkg.planning.filtering.latticized_filter import LatticedChecker
from pkg.planning.filtering.task_clearance_filter import TaskClearanceChecker

gcheck = GraspChecker(pscene)
rcheck = ReachChecker(pscene)
tcheck = TaskClearanceChecker(pscene, gcheck)
checkers_all = [tcheck, rcheck, gcheck]
# lcheck = LatticedChecker(pscene, gcheck)
# checkers_all.append(lcheck)
mplan.motion_filters = checkers_all
gscene.show_pose(crob.home_pose)

from pkg.planning.constraint.constraint_common \
            import sample_redundancy, combine_redundancy
gtimer = GlobalTimer.instance()
initial_state = pscene.initialize_state(crob.home_pose, force_fit_binding=True)

# remove place points except for the current one
use_current_place_point_only(pscene, initial_state)

gscene.update_markers_all()
print("subjects: {}".format(pscene.subject_name_list))
print("initial node: {}".format(initial_state.node))

subjects: ['box3', 'long_1', 'sweep1', 'sweep2', 'sweep3']
initial node: ('track_face', 'track_face', 0, 0, 0)


# CustomRule

In [18]:
from pkg.planning.task.custom_rules.sweep_entrance_control import SweepEntranceControlRule
from pkg.planning.constraint.constraint_common import get_binding_margins, fit_binding
from pkg.utils.traj_utils import simplify_schedule, mix_schedule
tplan.custom_rule = SweepEntranceControlRule(pscene)


# ## sampler
# from pkg.planning.sampling.node_sampling import make_state_param_hashable, UniformNodeSampler, PenaltyNodeSampler, GrowingSampler

# tplan.new_node_sampler = PenaltyNodeSampler(3, 1)
# tplan.parent_node_sampler = UniformNodeSampler(3)
# # tplan.parent_snode_sampler = GrowingSampler(3)

## Detect once

In [19]:
mplan.reset_log(False)
gtimer.reset()

with gtimer.block("detect"):
    for sname in pscene.subject_name_list:
        if isinstance(pscene.subject_dict[sname], AbstractObject):
            pscene.remove_subject(sname)
            
    gscene.clear_non_fixed()
    
    ## detect again
    gtem_dict = s_builder.detect_and_register(level_mask=[DetectionLevel.MOVABLE])

    ## create boxes
    box_list =  [] 
    for gname in sorted(gtem_dict.keys()):
        box_new = pscene.create_subject(oname=gname, gname=gname, _type=BoxObject, hexahedral=True)
        box_new.register_binders(pscene, PlacePlane)
        box_list.append(box_new)
    
    initial_state = pscene.initialize_state(crob.home_pose, force_fit_binding=True)
    initial_state = pscene.initialize_state(crob.home_pose, force_fit_binding=True)
    gscene.update_markers_all()

    # remove place points and sub-binders except for the current ones
    use_current_place_point_only(pscene, initial_state)
    use_current_sub_binders_only(pscene, initial_state)
    tplan.prepare()
    mplan.update_gscene()

## Plan & execute

In [20]:
from pkg.planning.constraint.constraint_common import get_binding_margins, fit_binding
from pkg.planning.motion.moveit.moveit_py import PlannerConfig
mplan.incremental_constraint_motion = True
config_dict =crob.get_robot_config_dict()
no_sdk_dict = {rname: "no_sdk" in config_dict[rname].specs and config_dict[rname].specs["no_sdk"] for rname in crob.robot_names}
indy0_vel_lim = 0.8
indy0_acc_lim = 1.5
indy1.traj_vel = 4
with indy1:
    indy1.set_joint_vel_level(3)

Connect: Server IP (192.168.21.2)


### Test gripper

In [21]:
crob.grasp(True, True)
time.sleep(0.5)
crob.grasp(False, False)

Connect: Server IP (192.168.21.2)
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.2)
Connect: Server IP (192.168.21.6)


### Test motion

In [22]:
crob.joint_move_make_sure(crob.home_pose+0.05)

Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.2)


In [23]:
crob.joint_move_make_sure(crob.home_pose)

Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.2)


## Run

In [24]:
from pkg.planning.motion.moveit.moveit_py import PlannerConfig
from multiprocessing import Process

In [27]:
while True:
    with indy0:
        indy0.wait_di(8,period=1)
    with indy0:
        indy0.direct_teaching(True)
    with indy1:
        indy1.direct_teaching(True)
    time.sleep(1)
    with indy0:
        di_in = int(indy0.get_di()[8])
        if di_in:
            indy0.direct_teaching(False)
    if di_in:
        with indy1:
            indy1.direct_teaching(False)
        TextColors.YELLOW.println("STOP: user command")
        break

    mplan.reset_log(False)
    gtimer.reset()
    
    with gtimer.block("detect"):
        for sname in pscene.subject_name_list:
            if isinstance(pscene.subject_dict[sname], AbstractObject):
                pscene.remove_subject(sname)
    
        gscene.clear_non_fixed()

        ## detect again
        gtem_dict = s_builder.detect_and_register(level_mask=[DetectionLevel.MOVABLE])

        ## create boxes
        box_list =  [] 
        for gname in sorted(gtem_dict.keys()):
            box_new = pscene.create_subject(oname=gname, gname=gname, _type=BoxObject, 
                                            hexahedral=True)
            box_new.register_binders(pscene, PlacePlane)
            box_list.append(box_new)

        initial_state = pscene.initialize_state(crob.home_pose, force_fit_binding=True)
        initial_state = pscene.initialize_state(crob.home_pose, force_fit_binding=True)
        gscene.update_markers_all()

        # remove place points and sub-binders except for the current ones
        use_current_place_point_only(pscene, initial_state)
        use_current_sub_binders_only(pscene, initial_state)
        tplan.prepare()
        mplan.update_gscene()

    print(initial_state.node)

    gtimer.tic("firstmove")
    obj_num = len(gtem_dict)
    sweep_num = len(sweep_list)
    from_state = initial_state
    t_exe = None
    snode_schedule_all = []
    for sweep_idx in range(sweep_num):
        gcheck.put_banned = [track_list[sweep_idx][2]]
        sweep_goal = tuple([int(i_s<=sweep_idx)*2 for i_s in range(sweep_num)])
    #     sweep_goal = tuple([int(i_s<=sweep_idx)*2 for i_s in range(2)])+(0,)
        goal_nodes = [("track_face",)*obj_num+sweep_goal]
        if sweep_idx < sweep_num-1:
            for i_s in range(obj_num):
                obj_goal = ["track_face"]*obj_num
                obj_goal[i_s] = "grip1"
                goal_nodes += [tuple(obj_goal)+sweep_goal]
        gtimer.tic("plan{}".format(sweep_idx))
        ppline.search(from_state, goal_nodes, verbose=False, display=False, dt_vis=0.01, 
                      timeout_loop=10, multiprocess=True, timeout=0.5, timeout_constrained=5, 
                      add_homing=False, post_optimize=False, max_solution_count=10)
        gtimer.toc("plan{}".format(sweep_idx))
        snode_schedule = ppline.tplan.get_best_schedule(at_home=False)
        if len(snode_schedule)==0:
            gtimer.tic("plan{}".format(sweep_idx))
            ppline.search(from_state, goal_nodes, verbose=False, display=False, dt_vis=0.01, 
                          timeout_loop=30, multiprocess=True, timeout=0.5, timeout_constrained=5, 
                          add_homing=False, post_optimize=False, max_solution_count=1)
            gtimer.toc("plan{}".format(sweep_idx))
            snode_schedule = ppline.tplan.get_best_schedule(at_home=False)
            
        snode_schedule += ppline.add_return_motion(snode_schedule[-1], initial_state=None, 
                                                   timeout=1, try_count=3)
    #     snode_schedule_wps = simplify_schedule(pscene, snode_schedule_ori, step_fractions=[0,1])
    #     snode_schedule_safe = bspline_simple_schedule(pscene, snode_schedule_wps, 0.5, 1)
        snode_schedule_simple = simplify_schedule(pscene, snode_schedule)
        snode_schedule_simple = recursive_shortcut_snode_schedule(pscene, mplan, snode_schedule_simple)
    #     snode_schedule_safe = calculate_safe_schedule(pscene, snode_schedule_simple, 0.5, 1)
        snode_schedule_safe = []
        snode_pre = None
        for snode in snode_schedule_simple:
            if snode.traj is None:
                snode_schedule_safe.append(snode)
            else:
                robots_in_act = crob.get_robots_in_act(snode.traj, skip_not_connected=False)
                if all(map(lambda namepair: no_sdk_dict[namepair[0]], robots_in_act)):
                    snode_schedule_safe.append(snode)
                else:
                    snode_schedule_safe += calculate_safe_schedule(pscene, [snode], 
                                                                   indy0_vel_lim, indy0_acc_lim)
            snode_pre = snode
    #     double_sweep_motions(snode_schedule_safe)
    #     snode_schedule = snode_schedule_safe
    #     snode_schedule = mix_schedule(mplan, snode_schedule_safe)
        snode_schedule = snode_schedule_safe
        from_state = snode_schedule[-1].state
        if t_exe is not None:
            t_exe.join()
            if not ppline.execute_res:
                TextColors.RED.println("STOP: Previous execution failed")
                raise(RuntimeError("STOP: Previous execution failed"))
        else:
            gtimer.toc("firstmove")
            with indy0:
                indy0.direct_teaching(False)
            with indy1:
                indy1.direct_teaching(False)
            time.sleep(0.5)
    #     ppline.execute_schedule(snode_schedule,
    #                             **dict(
    #                                 auto_stop=False, mode_switcher=ModeSwitcher(pscene),
    #                                 multiproc=False, error_stop_deg=None, one_by_one=True, auto_sync_robot_pose=True)
    #                            )
#         t_exe = Thread(target=ppline.execute_schedule, args = (snode_schedule,), 
#                         kwargs=dict(
#                             auto_stop=False, mode_switcher=ModeSwitcher(pscene),
#                             multiproc=False, error_stop_deg=None, one_by_one=True, auto_sync_robot_pose=True))
        t_exe = Process(target=ppline.execute_schedule, args = (snode_schedule,), 
                        kwargs=dict(
                            auto_stop=False, mode_switcher=ModeSwitcher(pscene),
                            multiproc=False, error_stop_deg=None, one_by_one=True, auto_sync_robot_pose=True))
        t_exe.daemon = True
        t_exe.start()
        snode_schedule_all.append(snode_schedule)
    #     break

    if t_exe is not None:
        t_exe.join()

    if ppline.execute_res:
        crob.stop_tracking()
        crob.joint_move_make_sure(crob.home_pose)
    # else:
    #     break

Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.2)
Connect: Server IP (192.168.21.6)
('track_face', 'track_face', 0, 0, 0)
Use 36/36 agents
Goal reached
Goal reached
Goal reached
Goal reached
Goal reached
Goal reached
Goal reached
Goal reached
Goal reached
Goal reached
Goal reached
======================= terminated 0: required answers acquired from other agent ===============================
======================= terminated 16: required answers acquired ===============================
======================= terminated 18: required answers acquired from other agent ===============================
======================= terminated 25: required answers acquired from other agent ===============================
======================= terminated 4: required answers acquired from other agent ===============================
======================= terminated 23: required answers acquired from other agent ===============================
=

======================= terminated 31: required answers acquired from other agent ===============================
======================= terminated 14: required answers acquired from other agent ===============================
Goal reached
======================= terminated 6: required answers acquired ===============================
======================= terminated 29: required answers acquired from other agent ===============================
======================= terminated 3: required answers acquired from other agent ===============================
======================= terminated 5: required answers acquired from other agent ===============================
======================= terminated 28: required answers acquired from other agent ===============================
======================= terminated 17: required answers acquired from other agent ===============================
======================= terminated 30: required answers acquired from other agent =============

======================= terminated 22: required answers acquired from other agent ===============================
======================= terminated 33: required answers acquired from other agent ===============================
======================= terminated 10: required answers acquired from other agent ===============================
======================= terminated 35: required answers acquired from other agent ===============================
======================= terminated 24: required answers acquired from other agent ===============================
Goal reached
======================= terminated 1: required answers acquired from other agent ===============================
======================= terminated 28: required answers acquired from other agent ===============================
======================= terminated 19: required answers acquired from other agent ===============================
======================= terminated 5: required answers acquired ============

rname: None
binder: brush_face
rname: indy0
Connect: Server IP (192.168.21.2)
Connect: Server IP (192.168.21.6)
http://192.168.21.6:9990/param_setting?control_force0=1
Connect: Server IP (192.168.21.2)
http://192.168.21.6:9990/param_setting?control_force0=0
binder: None
binder: grip1
rname: indy1
binder: None
binder: track_face
rname: None
binder: brush_face
rname: indy0
Connect: Server IP (192.168.21.2)
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.2)
binder: None
binder: grip1
rname: indy1
binder: None
binder: track_face
rname: None
binder: brush_face
rname: indy0
Connect: Server IP (192.168.21.2)
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.6)
Use 36/36 agents
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.2)
Connect: Server IP (192.168.21.2)
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED!

ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
Goal reached
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
Move finished!
Connect: Server IP (192.168.21.2)
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
Go

...

======================= terminated 19: required answers acquired from other agent ===============================
======================= terminated 11: required answers acquired from other agent ===============================
======================= terminated 12: required answers acquired from other agent ===============================
======================= terminated 25: required answers acquired from other agent ===============================
Goal reached
======================= terminated 7: required answers acquired ===============================
======================= terminated 22: required answers acquired from other agent ===============================
Goal reached
Goal reached
0 connection 0-1 : 3 -> 3
1 connection 1-4 : 3 -> 3
2 connection 4-10 : 3 -> 3
3 connection 10-205 : 2 -> 2
4 connection 205-211 : 2 -> 2
5 connection 211-234 : skip constrained
6 connection 234-274 : 4 -> 4
7 connection 274-275 : 3 -> 2
Connect: Server IP (192.168.21.6)
Connect: Server IP (192

======================= terminated 12: max iteration time reached (1634194185/1634194175.63 s) ===============================
======================= terminated 10: max iteration time reached (1634194185/1634194175.63 s) ===============================
======================= terminated 26: max iteration time reached (1634194185/1634194175.63 s) ===============================
======================= terminated 21: max iteration time reached (1634194185/1634194175.63 s) ===============================
======================= terminated 19: max iteration time reached (1634194185/1634194175.63 s) ===============================
======================= terminated 7: max iteration time reached (1634194185/1634194175.63 s) ===============================
======================= terminated 18: max iteration time reached (1634194185/1634194175.63 s) ===============================
======================= terminated 34: max iteration time reached (1634194185/1634194175.63 s) =================

ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
Move finished!
Connect: Server IP (192.168.21.2)
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
Connect: Server IP (192.168.21.2)
binder: None
binder: track_face
rname: None
binder: None
binder: grip1
rname: indy1
binder: brush_face
rname: indy0
Connect: Server IP (192.168.21.2)
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with initial state
connection failed but no other new node - retry previous one
ERROR sampling parent - NO SAMPLE REMAINED! Re-Start with 

Goal reached
Goal reached
Goal reached
Goal reached
======================= terminated 0: required answers acquired ===============================
======================= terminated 12: required answers acquired ===============================
======================= terminated 24: required answers acquired from other agent ===============================
======================= terminated 31: required answers acquired from other agent ===============================
======================= terminated 20: required answers acquired from other agent ===============================
======================= terminated 26: required answers acquired from other agent ===============================
======================= terminated 22: required answers acquired from other agent ===============================
======================= terminated 32: required answers acquired from other agent ===============================
======================= terminated 25: required answers acquired from o

======================= terminated 30: required answers acquired from other agent ===============================
======================= terminated 29: required answers acquired from other agent ===============================
======================= terminated 1: required answers acquired from other agent ===============================
======================= terminated 9: required answers acquired from other agent ===============================
======================= terminated 6: required answers acquired from other agent ===============================
======================= terminated 8: required answers acquired from other agent ===============================
Connect: Server IP (192.168.21.2)
Goal reached
0 connection 0-11 : 2 -> 2
1 connection 11-65 : 5 -> 5
2 connection 65-129 : 2 -> 2
3 connection 129-145 : 4 -> 4
4 connection 145-163 : 3 -> 3
5 connection 163-188 : skip constrained
6 connection 188-204 : 3 -> 2
Move finished!
Connect: Server IP (192.168.21.2)
Connect: S

## Stop 

In [20]:
crob.stop_tracking()
crob.joint_move_make_sure(crob.home_pose)

Connect: Server IP (192.168.0.63)
Connect: Server IP (192.168.0.63)
Connect: Server IP (192.168.0.63)


In [13]:
for snode_schedule in snode_schedule_all:
    ppline.play_schedule(snode_schedule, period=0.001)

('track_face', 'track_face', 0, 0, 0)->('track_face', 'track_face', 0, 0, 0)
('track_face', 'track_face', 0, 0, 0)->('track_face', 'grip1', 0, 0, 0)
('track_face', 'grip1', 0, 0, 0)->('track_face', 'grip1', 1, 0, 0)
('track_face', 'grip1', 1, 0, 0)->('track_face', 'grip1', 2, 0, 0)
('track_face', 'grip1', 2, 0, 0)->('track_face', 'grip1', 2, 0, 0)


In [27]:
indy1.traj_vel = 5
with indy1:
    indy1.set_joint_vel_level(3)

Connect: Server IP (192.168.0.106)


In [ ]:
raise(RuntimeError("Below is for testing - preventing auto run"))

## Plan & show

In [16]:
from pkg.planning.motion.moveit.moveit_py import PlannerConfig
mplan.incremental_constraint_motion = True
config_dict =crob.get_robot_config_dict()
no_sdk_dict = {rname: "no_sdk" in config_dict[rname].specs and config_dict[rname].specs["no_sdk"] for rname in crob.robot_names}

In [17]:
mplan.reset_log(False)
gtimer.reset()

with gtimer.block("detect"):
    for sname in pscene.subject_name_list:
        if isinstance(pscene.subject_dict[sname], AbstractObject):
            pscene.remove_subject(sname)
            
    gscene.clear_non_fixed()
    
    ## detect again
    gtem_dict = s_builder.detect_and_register(level_mask=[DetectionLevel.MOVABLE])

    ## create boxes
    box_list =  [] 
    for gname in sorted(gtem_dict.keys()):
        box_new = pscene.create_subject(oname=gname, gname=gname, _type=BoxObject, hexahedral=True)
        box_new.register_binders(pscene, PlacePlane)
        box_list.append(box_new)
    
    initial_state = pscene.initialize_state(crob.home_pose, force_fit_binding=True)
    initial_state = pscene.initialize_state(crob.home_pose, force_fit_binding=True)
    gscene.update_markers_all()

    # remove place points and sub-binders except for the current ones
    use_current_place_point_only(pscene, initial_state)
    use_current_sub_binders_only(pscene, initial_state)
    tplan.prepare()
    mplan.update_gscene()
    
print(initial_state.node)

gtimer.tic("firstmove")
obj_num = len(gtem_dict)
sweep_num = len(sweep_list)
from_state = initial_state
t_exe = None
snode_schedule_all = []
for sweep_idx in range(sweep_num):
    gcheck.put_banned = [track_list[sweep_idx][2]]
    sweep_goal = tuple([int(i_s<=sweep_idx)*2 for i_s in range(sweep_num)])
#     sweep_goal = tuple([int(i_s<=sweep_idx)*2 for i_s in range(2)])+(0,)
    goal_nodes = [("track_face",)*obj_num+sweep_goal]
    if sweep_idx < sweep_num-1:
        for i_s in range(obj_num):
            obj_goal = ["track_face"]*obj_num
            obj_goal[i_s] = "grip1"
            goal_nodes += [tuple(obj_goal)+sweep_goal]
    gtimer.tic("plan{}".format(sweep_idx))
    ppline.search(from_state, goal_nodes, verbose=False, display=False, dt_vis=0.01, 
                  timeout_loop=100, multiprocess=True, timeout=0.5, timeout_constrained=2, 
                  add_homing=False, post_optimize=False, max_solution_count=10)
    gtimer.toc("plan{}".format(sweep_idx))
    snode_schedule = ppline.tplan.get_best_schedule(at_home=False)
    snode_schedule += ppline.add_return_motion(snode_schedule[-1], initial_state=None, timeout=0.5, try_count=3)
#     snode_schedule_wps = simplify_schedule(pscene, snode_schedule_ori, step_fractions=[0,1])
#     snode_schedule_safe = bspline_simple_schedule(pscene, snode_schedule_wps, 0.5, 1)
    snode_schedule_simple = simplify_schedule(pscene, snode_schedule)
#     snode_schedule_safe = calculate_safe_schedule(pscene, snode_schedule_simple, 0.5, 1)
    snode_schedule_safe = []
    for snode in snode_schedule_simple:
        if snode.traj is None:
            snode_schedule_safe.append(snode)
            continue
        else:
            robots_in_act = crob.get_robots_in_act(snode.traj, skip_not_connected=False)
            if all(map(lambda namepair: no_sdk_dict[namepair[0]], robots_in_act)):
                snode_schedule_safe.append(snode)
                continue
            else:
                snode_schedule_safe += calculate_safe_schedule(pscene, [snode], 0.5, 1)
#     double_sweep_motions(snode_schedule_safe)
#     snode_schedule = snode_schedule_safe
#     snode_schedule = mix_schedule(mplan, snode_schedule_safe)
    snode_schedule = snode_schedule_safe
    from_state = snode_schedule[-1].state
    if t_exe:
        t_exe.join()
    else:
        if len(snode_schedule_all)==0:
            gtimer.toc("firstmove")
    snode_schedule_all.append(snode_schedule)
#     t_exe = Thread(target=ppline.play_schedule, args = (snode_schedule,), kwargs=dict( period=0.01))
#     t_exe.start()
# t_exe.join()

('track_face', 'long_1_back', 'track_face', 0, 0, 0)
Use 36/36 agents
try: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'long_1_back', 'track_face', 1, 0, 0)
Motion Filer Failure: TaskClearanceChecker
try: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('grip1', 'long_1_back', 'track_face', 0, 0, 0)
result: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'long_1_back', 'track_face', 1, 0, 0) = fail
try transition motion
try: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'long_1_back', 'grip1', 0, 0, 0)
try: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('grip1', 'long_1_back', 'track_face', 0, 0, 0)
Motion Filer Failure: ReachChecker
try: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'long_1_back', 'grip1', 0, 0, 0)
result: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'long_1_back', 'grip1', 0, 0, 0) = fail
try transition motion
t

Motion Filer Failure: GraspChecker
Motion Filer Failure: GraspChecker
try: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'grip1', 'track_face', 0, 0, 0)
try: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'long_1_back', 'grip1', 0, 0, 0)
try: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'grip1', 'track_face', 0, 0, 0)
try: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'grip1', 'track_face', 0, 0, 0)
Motion Plan Failure
result: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'long_1_back', 'grip1', 0, 0, 0) = fail
Motion Filer Failure: ReachChecker
result: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'grip1', 'track_face', 0, 0, 0) = fail
try: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'grip1', 'track_face', 0, 0, 0)
Motion Filer Failure: ReachChecker
try transition motion
result: 0 - ('track_face',

Motion Filer Failure: GraspChecker
try joint motion
transition motion tried: False
try: 6 - ('track_face', 'long_1_back', 'grip1', 0, 0, 0)->('track_face', 'long_1_back', 'grip1', 0, 0, 0)
Motion Filer Failure: TaskClearanceChecker
joint motion tried: True
result: 3 - ('grip1', 'long_1_back', 'track_face', 0, 0, 0)->('grip1', 'long_1_back', 'track_face', 1, 0, 0) = fail
try: 7 - ('track_face', 'long_1_back', 'grip1', 0, 0, 0)->('track_face', 'long_1_back', 'grip1', 1, 0, 0)
try: 7 - ('track_face', 'long_1_back', 'grip1', 0, 0, 0)->('track_face', 'long_1_back', 'grip1', 0, 0, 0)
try: 8 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'long_1_back', 'track_face', 0, 0, 0)
result: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'long_1_back', 'grip1', 0, 0, 0) = fail
result: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'grip1', 'track_face', 0, 0, 0) = fail
try: 6 - ('track_face', 'long_1_back', 'grip1', 0, 0, 0)->

Motion Filer Failure: GraspChecker
Motion Filer Failure: GraspChecker
result: 5 - ('track_face', 'grip1', 'track_face', 0, 0, 0)->('track_face', 'track_face', 'track_face', 0, 0, 0) = fail
result: 7 - ('track_face', 'long_1_back', 'grip1', 0, 0, 0)->('track_face', 'long_1_back', 'grip1', 0, 0, 0) = success
try: 12 - ('track_face', 'grip1', 'track_face', 0, 0, 0)->('track_face', 'grip1', 'track_face', 1, 0, 0)
branching: 0->11 (1.69/100.0 s, steps/err: 127(678.539037704 ms)/0.00143788593326)
result: 4 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'long_1_back', 'grip1', 0, 0, 0) = fail
branching: 0->12 (1.69/100.0 s, steps/err: 24(452.303171158 ms)/0.00155987924217)
result: 10 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'long_1_back', 'track_face', 1, 0, 0) = fail
try: 12 - ('track_face', 'grip1', 'track_face', 0, 0, 0)->('track_face', 'grip1', 'track_face', 0, 0, 0)
try: 5 - ('track_face', 'grip1', 'track_face', 0, 0, 0)->('track_face

try: 14 - ('track_face', 'grip1', 'track_face', 0, 0, 0)->('track_face', 'track_face', 'track_face', 0, 0, 0)
try: 4 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'grip1', 'track_face', 0, 0, 0)
result: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('grip1', 'long_1_back', 'track_face', 0, 0, 0) = fail
try: 4 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'long_1_back', 'grip1', 0, 0, 0)
result: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('grip1', 'long_1_back', 'track_face', 0, 0, 0) = fail
try: 8 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'grip1', 'track_face', 0, 0, 0)
result: 6 - ('track_face', 'long_1_back', 'grip1', 0, 0, 0)->('track_face', 'long_1_back', 'grip1', 0, 0, 0) = success
try: 0 - ('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('grip1', 'long_1_back', 'track_face', 0, 0, 0)
result: 1 - ('grip1', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'long_1_bac

...

result: 2886 - ('grip1', 'long_1_back', 'track_face', 2, 0, 0)->('grip1', 'long_1_back', 'track_face', 2, 1, 0) = fail
Motion Filer Failure: TaskClearanceChecker
transition motion tried: False
result: 300 - ('track_face', 'long_1_back', 'track_face', 2, 0, 0)->('track_face', 'long_1_back', 'grip1', 2, 0, 0) = fail
result: 2865 - ('track_face', 'long_1_back', 'grip1', 2, 0, 0)->('track_face', 'long_1_back', 'grip1', 2, 0, 0) = success
Motion Filer Failure: GraspChecker
joint motion tried: False
try joint motion
try: 2888 - ('grip1', 'long_1_back', 'track_face', 2, 0, 0)->('grip1', 'long_1_back', 'track_face', 2, 1, 0)
result: 2887 - ('track_face', 'long_1_back', 'track_face', 2, 0, 0)->('track_face', 'long_1_back', 'track_face', 2, 1, 0) = fail
branching: 84->2888 (99.92/100.0 s, steps/err: 23(553.020000458 ms)/0.00190252151731)
result: 786 - ('track_face', 'long_1_back', 'track_face', 2, 0, 0)->('track_face', 'long_1_back', 'grip1', 2, 0, 0) = fail
Motion Plan Failure
branching: 2865->

======================= terminated 5: max iteration time reached (1633942352/1633942252.4 s) ===============================
branching: 49->2895 (100.11/100.0 s, steps/err: 45(802.668094635 ms)/0.000806637655776)
joint motion tried: False
======================= terminated 4: max iteration time reached (1633942352/1633942252.4 s) ===============================
======================= terminated 7: max iteration time reached (1633942352/1633942252.4 s) ===============================
Motion Plan Failure
branching: 2880->2894 (100.11/100.0 s, steps/err: 66(441.381216049 ms)/0.0389929062035)
======================= terminated 26: max iteration time reached (1633942352/1633942252.4 s) ===============================
Motion Plan Failure
======================= terminated 19: max iteration time reached (1633942352/1633942252.4 s) ===============================
======================= terminated 30: max iteration time reached (1633942352/1633942252.4 s) ===============================
resul

======================= terminated 9: max iteration time reached (1633942352/1633942252.4 s) ===============================
end
constrained motion tried: True
result: 49 - ('track_face', 'long_1_back', 'grip1', 1, 0, 0)->('track_face', 'long_1_back', 'grip1', 2, 0, 0) = success
transition motion tried: True
branching: 49->2901 (100.39/100.0 s, steps/err: 45(523.633003235 ms)/0.000806637655776)
result: 84 - ('track_face', 'long_1_back', 'track_face', 2, 0, 0)->('grip1', 'long_1_back', 'track_face', 2, 0, 0) = success
======================= terminated 0: max iteration time reached (1633942352/1633942252.4 s) ===============================
branching: 84->2902 (100.4/100.0 s, steps/err: 93(358.704090118 ms)/0.00108993365813)
======================= terminated 33: max iteration time reached (1633942352/1633942252.4 s) ===============================
end
constrained motion tried: True
end
constrained motion tried: True
result: 49 - ('track_face', 'long_1_back', 'grip1', 1, 0, 0)->('track_

IndexError: list index out of range

generate table - Geometry
generate table - Handle
generate table - Object
generate table - Binder
generate table - PlanConditions
generate table - PlanList
button clicked
('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('grip1', 'long_1_back', 'track_face', 0, 0, 0)
('grip1', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'long_1_back', 'track_face', 0, 0, 0)
('track_face', 'long_1_back', 'track_face', 0, 0, 0)->('track_face', 'long_1_back', 'grip1', 0, 0, 0)
('track_face', 'long_1_back', 'grip1', 0, 0, 0)->('track_face', 'long_1_back', 'grip1', 0, 0, 0)
('track_face', 'long_1_back', 'grip1', 0, 0, 0)->('track_face', 'long_1_back', 'grip1', 1, 0, 0)
('track_face', 'long_1_back', 'grip1', 1, 0, 0)->('track_face', 'long_1_back', 'grip1', 2, 0, 0)
button action done


In [18]:
print(gtimer)

detect: 	604.7 ms/1 = 604.7 ms (604.691/604.691)
firstmove: 	16615.8 ms/1 = 16615.8 ms (16615.812/16615.812)
plan0: 	15611.9 ms/1 = 15611.9 ms (15611.925/15611.925)
initialize_memory: 	48.8 ms/3 = 16.3 ms (13.663/21.165)
init_search: 	24.1 ms/3 = 8.0 ms (6.311/10.895)
start_process: 	6787.0 ms/3 = 2262.3 ms (2196.32/2389.592)
wait_procs: 	492193.6 ms/75 = 6562.6 ms (500.706/13598.053)
wait_procs_extra: 	557214.9 ms/396 = 1407.1 ms (0.003/2478.713)
plan1: 	17787.6 ms/1 = 17787.6 ms (17787.568/17787.568)
plan2: 	17229.9 ms/1 = 17229.9 ms (17229.895/17229.895)



In [19]:
# for i_ss, snode_schedule in enumerate(snode_schedule_all):
#     for i_s, snode in enumerate(snode_schedule):
#         if snode.traj is not None:
#             save_json("data/traj_{}_{}.json".format(i_ss, i_s), snode.traj[:,:6])

## mix full schedule

In [20]:
gtimer.reset()
snode_schedule_cat = [snode_schedule_all[0][0]]
for snode_schedule in snode_schedule_all:
    snode_schedule_cat += snode_schedule[1:]

# with gtimer.block("mix_schedule_safe"):
#     safe_mixed = mix_schedule(mplan, snode_schedule_cat)

# print(gtimer)

safe_mixed = snode_schedule_cat

### play schedule

In [21]:
ppline.play_schedule(safe_mixed, period=0.001)

('track_face', 'track_face', 'track_face', 0, 0, 0)->('track_face', 'grip1', 'track_face', 0, 0, 0)
('track_face', 'grip1', 'track_face', 0, 0, 0)->('track_face', 'track_face', 'track_face', 0, 0, 0)
('track_face', 'track_face', 'track_face', 0, 0, 0)->('track_face', 'track_face', 'grip1', 0, 0, 0)
('track_face', 'track_face', 'grip1', 0, 0, 0)->('track_face', 'track_face', 'grip1', 0, 0, 0)
('track_face', 'track_face', 'grip1', 0, 0, 0)->('track_face', 'track_face', 'grip1', 1, 0, 0)
('track_face', 'track_face', 'grip1', 1, 0, 0)->('track_face', 'track_face', 'grip1', 2, 0, 0)
('track_face', 'track_face', 'grip1', 2, 0, 0)->('track_face', 'track_face', 'grip1', 2, 0, 0)
('track_face', 'track_face', 'grip1', 2, 0, 0)->('track_face', 'track_face', 'grip1', 2, 0, 0)
('track_face', 'track_face', 'grip1', 2, 0, 0)->('track_face', 'track_face', 'track_face', 2, 0, 0)
('track_face', 'track_face', 'track_face', 2, 0, 0)->('track_face', 'grip1', 'track_face', 2, 0, 0)
('track_face', 'grip1', '

In [21]:
# ppline.play_schedule(safe_mixed[:1], period=0.001)
# color_off = (0.8,0.2,0.2,0.2)
# for obj_name in ppline.pscene.subject_name_list:
#     if isinstance(ppline.pscene.subject_dict[obj_name], AbstractTask):
#         actor, obj = ppline.pscene.actor_dict['brush_face'], ppline.pscene.subject_dict[obj_name]
#         for gtem in obj.clearance:
#             gtem.color = color_off
#             ppline.pscene.gscene.update_marker(gtem)
#             ppline.pscene.set_object_state(snode_schedule_all[0][0].state)
# ppline.pscene.gscene.update_markers_all()

In [22]:
# from pkg.utils.code_scraps import play_schedule_clearance_highlight
# play_schedule_clearance_highlight(ppline, safe_mixed, tcheck=tcheck, period=0.001)

### Run fully mixed schedule

In [32]:
from pkg.planning.constraint.constraint_common import get_binding_margins, fit_binding
crob.reset_connection(True,True)

connection command:
indy0: True
indy1: True
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.2)


In [33]:
crob.stop_tracking()

Connect: Server IP (192.168.21.6)


In [34]:
indy0 = crob.robot_dict["indy0"]
indy1 = crob.robot_dict["indy1"]

indy1.grasp_ref = False
with indy1:
    indy1.set_joint_vel_level(1)

with indy0:
    indy0.reset()
    
with indy1:
    indy1.reset()
    
time.sleep(3)

Connect: Server IP (192.168.21.2)
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.2)
Connect: Server IP (192.168.21.2)


In [35]:
crob.grasp(True, True)
time.sleep(0.5)
crob.grasp(False, False)

Connect: Server IP (192.168.21.2)
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.2)
Connect: Server IP (192.168.21.6)


In [41]:
crob.joint_move_make_sure(crob.home_pose+([0]*6+[0,0,0,0,np.deg2rad(60),0]))

Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.2)


In [40]:
crob.joint_move_make_sure(crob.home_pose+0.05)

Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.2)


In [41]:
crob.joint_move_make_sure(crob.home_pose)

Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.6)
Connect: Server IP (192.168.21.2)


In [26]:
ppline.execute_schedule(safe_mixed, mode_switcher=ModeSwitcher(pscene),
                        multiproc=False, error_stop_deg=None, one_by_one=True)

Connect: Server IP (192.168.0.106)
Connect: Server IP (192.168.0.106)
Connect: Server IP (192.168.0.106)
Move finished!
Connect: Server IP (192.168.0.106)
Connect: Server IP (192.168.0.106)
binder: None
binder: track_face
rname: None
binder: None
binder: grip1
rname: indy1
binder: None
Connect: Server IP (192.168.0.106)
Connect: Server IP (192.168.0.63)
Connect: Server IP (192.168.0.106)
Connect: Server IP (192.168.0.106)
Connect: Server IP (192.168.0.106)
Move finished!
Connect: Server IP (192.168.0.106)
Connect: Server IP (192.168.0.106)
binder: None
binder: track_face
rname: None
binder: None
binder: track_face
rname: None
binder: None
Connect: Server IP (192.168.0.106)
Connect: Server IP (192.168.0.63)
Connect: Server IP (192.168.0.106)
Connect: Server IP (192.168.0.106)
Connect: Server IP (192.168.0.106)
Move finished!
Connect: Server IP (192.168.0.106)
Connect: Server IP (192.168.0.106)
binder: None
binder: grip1
rname: indy1
binder: None
binder: track_face
rname: None
binder: No

True